In [1]:
#downloading libraries
import pandas as pd 
import numpy as np
import matplotlib as plt
import pandas as pd
import nltk
import re
import numpy as np
from nltk import word_tokenize
from nltk.corpus import stopwords
from string import punctuation
import matplotlib.pyplot as plt
from collections import Counter
import pickle

#nltk.download()
nltk.download('punkt')
nltk.download('stopwords')

[nltk_data] Downloading package punkt to C:\Users\Abhishek's
[nltk_data]     PC\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to C:\Users\Abhishek's
[nltk_data]     PC\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [2]:
from keras.layers import Dense, Dropout, Flatten  
from keras.layers import Conv2D, MaxPooling2D
import keras
from keras.layers import Dense, Conv2D
from keras.layers import Flatten
from keras.layers import MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Activation
from keras.layers import BatchNormalization
from keras.layers import Dropout
from keras.models import Sequential
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import SGDClassifier
from sklearn import model_selection
from sklearn.ensemble import AdaBoostClassifier

Using TensorFlow backend.


In [ ]:
import praw
import pprint
import pandas as pd
reddit = praw.Reddit(client_id='300HIOocldVcKA', client_secret='PCktLUhpPaRB1RrBCouEDPdpEBU', user_agent='abhishek chopra')
posts = []
india_subreddit = reddit.subreddit('India')
posts=[]
for post in india_subreddit.top('all',limit=1000):
    posts.append([post.title, post.score, post.id, post.url, post.num_comments, post.selftext, post.created,post.link_flair_text])
posts_pd = pd.DataFrame(posts,columns=['title', 'score', 'id', 'url', 'num_comments', 'body', 'created','flair'])

for post in india_subreddit.top('week',limit=1000):
    if post.title not in posts_pd['title'].unique():
         posts.append([post.title, post.score, post.id, post.url, post.num_comments, post.selftext, post.created,post.link_flair_text])
posts_pd = pd.DataFrame(posts,columns=['title', 'score', 'id', 'url', 'num_comments', 'body', 'created','flair'])

for post in india_subreddit.hot(limit=1000):
    if post.title not in posts_pd['title'].unique():
         posts.append([post.title, post.score, post.id, post.url, post.num_comments, post.selftext, post.created,post.link_flair_text])
posts_pd = pd.DataFrame(posts,columns=['title', 'score', 'id', 'url', 'num_comments', 'body', 'created','flair'])

for post in india_subreddit.new(limit=1000):
    if post.title not in posts_pd['title'].unique():
         posts.append([post.title, post.score, post.id, post.url, post.num_comments, post.selftext, post.created,post.link_flair_text])
posts_pd = pd.DataFrame(posts,columns=['title', 'score', 'id', 'url', 'num_comments', 'body', 'created','flair'])

In [ ]:
i=0
for flair in posts_pd['flair']:
    if flair == 'Unverified' or flair == 'AMA' or flair == 'AMA Concluded':
        posts_pd['flair'][i]='AMA'
        print(posts_pd['flair'][i])
    i=i+1
i=0
for flair in posts_pd['flair']:
    if flair == 'Policy & Economy' or flair == 'Policy' or flair == 'Demonetization' or flair == 'Policy/Economy ':
        posts_pd['flair'][i]='Policy/Economy'
        print(posts_pd['flair'][i])
    i=i+1   
i=0
for flair in posts_pd['flair']:
    if flair == 'Entertainment' or flair == 'Misleading' or flair == 'r/all' or flair == '/r/all':
        posts_pd['flair'][i]='Non-Political'
        print(posts_pd['flair'][i])
    i=i+1    
i=0
for flair in posts_pd['flair']:
    if flair == 'Science & Technology':
        posts_pd['flair'][i]='Science/Technology'
        print(posts_pd['flair'][i])
    i=i+1    
    
flair_list=['AMA','AskIndia','Business/Finance','Food','Non-Political','Photography','Policy/Economy','Politics','Science/Technology','Sports','[R]eddiquette']
i=0
for flair in posts_pd['flair']:
    if flair not in flair_list:
        posts_pd['flair'][i]='waste'
        print(posts_pd['flair'][i])
    i=i+1  

temp=[]
for i in range(len(posts_pd)):
    if posts_pd['flair'][i]!='waste':
        temp.append([posts_pd.title[i], posts_pd.score[i], posts_pd.id[i], posts_pd.url[i], posts_pd.num_comments[i], posts_pd.body[i], posts_pd.created[i],posts_pd.flair[i]])
posts_corr= pd.DataFrame(temp,columns=['title', 'score', 'id', 'url', 'num_comments', 'body', 'created','flair'])

In [ ]:
reddit = reddit = praw.Reddit(client_id='300HIOocldVcKA', client_secret='PCktLUhpPaRB1RrBCouEDPdpEBU', user_agent='abhishek chopra')

subreddit = reddit.subreddit('india')
topics_dict = {"flair":[], "title":[], "score":[], "id":[], "url":[], "body":[],"comms_num": [], "created": [], "comments":[]}
import datetime as dt
def date_convertor(data):
    return dt.datetime.fromtimestamp(data)

for flair in flair_list:
  
  get_subreddits = subreddit.search(flair, limit=100)
  
  for submission in get_subreddits:
    
    topics_dict["flair"].append(flair)
    topics_dict["title"].append(submission.title)
    topics_dict["score"].append(submission.score)
    topics_dict["id"].append(submission.id)
    topics_dict["url"].append(submission.url)
    topics_dict["body"].append(submission.selftext)
    topics_dict["comms_num"].append(submission.num_comments)
    topics_dict["created"].append(submission.created)
    
    submission.comments.replace_more(limit=None)
    comment = ''
    for top_level_comment in submission.comments:
        comment = comment + ' ' + top_level_comment.body
    topics_dict["comments"].append(comment)
    
topics_data = pd.DataFrame(topics_dict)
_timestamp = topics_data["created"].apply(date_convertor)
topics_data = topics_data.assign(timestamp = _timestamp)
del topics_data['created']
topics_data.to_csv('reddit-india-data.csv', index=False)

In [3]:
data=pd.read_csv('reddit-india-data.csv')
data

flair                                              title  score  \
0               AMA             I'm a Malayalee ABCD. Ask Me Anything.      1   
1               AMA  What are some of the memorable posts of r/India??     85   
2               AMA    Requesting AMA by Residents of Jammu & Kashmir.      4   
3               AMA  Friends, Indians, countrymen, I cleared UPSC C...   1859   
4               AMA                     So this happened yesterday [R]    609   
5               AMA  Congress social media head Divya Spandana dele...     78   
6               AMA  How magician like Karan Singh do such magics? ...      6   
7               AMA      [Question] Has anyone here tried Paytm First?      5   
8               AMA  AMA Request: A Kashmiri Pandit over 30 years old.     71   
9               AMA  I was searching for something and I stumbled u...    332   
10              AMA  #MenToo: The great Indian gender pushback, now...     19   
11              AMA  I am an Indian getting married to a Pakistani ...    265   
12              AMA  India's first indigenous processor developed a...   4390   
13              AMA  AMA Announcement: Atishi, member Political Aff...    145   
14              AMA        abcd here, anyone wanna be friends lol? ama      2   
15              AMA  I came to Delhi exactly 20 years back from Bih...     41   
16              AMA  Jallikattu caste clash: Violence after Dalit m...     63   
17              AMA    AMA of a common Delhiite and daily LNRDT poster     79   
18              AMA  Hey r/india, I am a Trader/Investor who made 1...    201   
19              AMA  As an Indian your first AMA happens when you t...    158   
20              AMA  Avi Gill - Paradise ft. Mista Baaz [Official M...      8   
21              AMA  [/r/IndianFootball] I am Aditi Chauhan, captai...     56   
22              AMA  I'm a 1.6lpm "elite" MBA who can't find a job....    180   
23              AMA  Is Vice (the movie) going to be released in In...     15   
24              AMA  Arnab Goswami misquotes Ambedkar, calls Mahatm...    168   
25              AMA           I am an officer of the Indian Navy. AMA.     27   
26              AMA  Before and after my Opti-LASIK procedure in Ba...    174   
27              AMA  AMA Announcement: Varun Grover and Vikramadity...    206   
28              AMA  IIT Alumni, and CEO of a drone making company ...     63   
29              AMA  Period. End of Sentence. | The Pad Project | N...      3   
...             ...                                                ...    ...   
988          Sports                        Any formula 1 fans in here?     18   
989          Sports  Swapna Burman, 6 toes in both legs, no money f...   3541   
990          Sports  NRI dies during adventurous sport at Hyderabad...     11   
991          Sports                                          Need help     15   
992          Sports          Where do I watch Formula 1 live in India?      6   
993          Sports  Star Sports not telecasting all Premier League...      2   
994          Sports                How about we don't watch TV at all.     55   
995          Sports  "India Was Such A Poor Place": Lewis Hamilton ...     99   
996          Sports  Gaming cult looks to level up in India. Thanks...     30   
997          Sports  Mumbai: Parkour athletes from UK perform stunt...    237   
998          Sports  Looking to meet fellow Sports aficionados and ...      1   
999          Sports                  The art of bargaining/negotiation     18   
1000  [R]eddiquette  [R]eddiquette Can I take earphones inside Eden...      5   
1001  [R]eddiquette  What positive culture did the Muslim conquests...     14   
1002  [R]eddiquette  ELI5: How come people can use words like "*tar...     15   
1003  [R]eddiquette  People of r/india, help a complete stranger ou...      1   
1004  [R]eddiquette        Planning for the Election [R]esult Coverage     67   
1005  [R]eddiquette  How the case of person w

In [4]:
data.to_json(r'reddit_data.json')

In [6]:
import pymongo
from pymongo import MongoClient
client = MongoClient()

In [7]:
import json

with open('reddit_data.json') as json_file:
    data = json.load(json_file)

In [8]:
data

{'flair': {'0': 'AMA',
  '1': 'AMA',
  '2': 'AMA',
  '3': 'AMA',
  '4': 'AMA',
  '5': 'AMA',
  '6': 'AMA',
  '7': 'AMA',
  '8': 'AMA',
  '9': 'AMA',
  '10': 'AMA',
  '11': 'AMA',
  '12': 'AMA',
  '13': 'AMA',
  '14': 'AMA',
  '15': 'AMA',
  '16': 'AMA',
  '17': 'AMA',
  '18': 'AMA',
  '19': 'AMA',
  '20': 'AMA',
  '21': 'AMA',
  '22': 'AMA',
  '23': 'AMA',
  '24': 'AMA',
  '25': 'AMA',
  '26': 'AMA',
  '27': 'AMA',
  '28': 'AMA',
  '29': 'AMA',
  '30': 'AMA',
  '31': 'AMA',
  '32': 'AMA',
  '33': 'AMA',
  '34': 'AMA',
  '35': 'AMA',
  '36': 'AMA',
  '37': 'AMA',
  '38': 'AMA',
  '39': 'AMA',
  '40': 'AMA',
  '41': 'AMA',
  '42': 'AMA',
  '43': 'AMA',
  '44': 'AMA',
  '45': 'AMA',
  '46': 'AMA',
  '47': 'AMA',
  '48': 'AMA',
  '49': 'AMA',
  '50': 'AMA',
  '51': 'AMA',
  '52': 'AMA',
  '53': 'AMA',
  '54': 'AMA',
  '55': 'AMA',
  '56': 'AMA',
  '57': 'AMA',
  '58': 'AMA',
  '59': 'AMA',
  '60': 'AMA',
  '61': 'AMA',
  '62': 'AMA',
  '63': 'AMA',
  '64': 'AMA',
  '65': 'AMA',
  '66': 'AM

In [9]:
client = MongoClient('mongodb://localhost:27017')

In [10]:
client

MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True)

In [11]:
db = client.reddit_flair_data

In [12]:
posts = db.posts

In [13]:
result = posts.insert_one(data)

ServerSelectionTimeoutError: localhost:27017: [WinError 10061] No connection could be made because the target machine actively refused it